In [1]:
#pip install nltk -U


In [2]:
import nltk
from nltk.corpus import stopwords
from pyhive import hive
import os
import pandas as pd
import re
import string
import numpy as np
import sys

nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [3]:
connection = hive.Connection(host="localhost",port=10000, auth="NOSASL",database="amazonreviews")
cursor = connection.cursor()
cursor.execute('set hive.execution.engine=mr')
cursor.execute('show databases')
cursor.fetchall()

[('amazonreviews',), ('default',), ('test',)]

In [4]:
cursor.execute('select * from amazonreviews.amazonToys limit 10000')
amazonToys = cursor.fetchall()
toysDataset = pd.DataFrame(amazonToys, columns=['reviewerID','reviewerName','reviewText','summary','reviewDate','category','class']);


In [5]:
spam_temp = toysDataset[toysDataset['class'] == 1] 
spam_dataset=pd.DataFrame(spam_temp)
ham_temp = toysDataset[toysDataset['class'] == 0]               #Considered non-spam as ham 
ham_dataset=pd.DataFrame(ham_temp) 

In [6]:
ham_dataset

reviewerID                   reviewerName  \
8     A1LGHTM5WB95MA                 Bill from Ohio   
21     A5JIJ6IRIFU1C                    SuZQ "SuZQ"   
28     AGEZCQIM4P2G9                   bobbie perez   
31     AMYF8VCWJB9WP  Mr. Hunchback "Mr. Hunchback"   
46    A213510DXNX99D                          Rob S   
...              ...                            ...   
9908  A2JZHXU0FLXHHY                        trooper   
9931  A157ISH0N5R6XE                        Lizhang   
9938  A2MBD3WA4L0CK7     Suzanne in Omaha "Suzanne"   
9939  A24PNVLQKEOZ2N                      Ben "Ben"   
9946  A2YNGLY35XSO3W                      Thomas J.   

                                             reviewText  \
8     Ok in good shape but missing a piece. We alrea...   
21    I got this game to use as an object lesson for...   
28    In order to finish this game there is a piece ...   
31    This Cobra Commander bust is a teeny tiny deli...   
46    I bought this so my younger family members cou...   
...                                                 ...   
9908  I have had Scrabble (the old version) for seve...   
9931  I suggest the quarter map should be renewed be...   
9938  I bought this for my 8 year old. Almost all th...   
9939  The product description needs to include the i...   
9946  Figures designed for chopper will not fit in c...   

                                          summary  reviewDate        category  \
8                                Ok in good shape  17-04-2014  Toys_and_Games   
21                Good for keystone demonstration  12-09-2009  Toys_and_Games   
28                                         broken  16-07-2013  Toys_and_Games   
31    REAL PRODUCT DIMENSIONS: 6 x 3 x 1.5 inches  04-12-2012  Toys_and_Games   
46                            Great Game; Bad Buy  08-01-2014  Toys_and_Games   
...                                           ...         ...             ...   
9908          very different from the old version  01-04-2011  Toys_and_Games   
9931                                renew the map  24-04-2009  Toys_and_Games   
9938             Very disappointed in the quality  03-01-2009  Toys_and_Games   
9939                                     Need IPD  17-10-2011  Toys_and_Games   
9946                            Not battle ready!  25-03-2007  Toys_and_Games   

      class  
8       0.0  
21      0.0  
28      0.0  
31      0.0  
46      0.0  
...     ...  
9908    0.0  
9931    0.0  
9938    0.0  
9939    0.0  
9946    0.0  

[1527 rows x 7 columns]

In [7]:
spam_mapperout = [];
for ind in spam_dataset.index:
    single_line =spam_dataset['reviewText'][ind]
    doc_id = spam_dataset['reviewerID'][ind]
    single_line = single_line.lower().strip()
    single_line = re.sub(r"[^\w\s]", "", single_line)
    words = single_line.split()
    for word in words:
        isDigits = any(str.isdigit(c) for c in word)
        if len(word) > 3 and not isDigits and word not in stopwords.words('english'):
            print(word, doc_id, 1)
            spam_mapperout.append((word, doc_id, 1))
    
    
    
    # print(ham_dataset.loc[i, "reviewerID"], ham_dataset.loc[i, "reviewerName"],ham_dataset.loc[i, "reviewText"],ham_dataset.loc[i, "summary"],ham_dataset.loc[i, "reviewDate"],ham_dataset.loc[i, "category"],ham_dataset.loc[i, "class"])

really A3SJS310YMX3IK 1
enjoy A3SJS310YMX3IK 1
wish A3SJS310YMX3IK 1
bigger A3SJS310YMX3IK 1
part A3SJS310YMX3IK 1
really A3SJS310YMX3IK 1
nice A3SJS310YMX3IK 1
cute A3SJS310YMX3IK 1
plushie A3T2KVP6795R2D 1
awesome A3T2KVP6795R2D 1
experience A3T2KVP6795R2D 1
arrived A3T2KVP6795R2D 1
quickly A3T2KVP6795R2D 1
even A3T2KVP6795R2D 1
better A3T2KVP6795R2D 1
hoped A3T2KVP6795R2D 1
would A3T2KVP6795R2D 1
napoleon A3UV7L5ND3EH8T 1
dynamite A3UV7L5ND3EH8T 1
movie A3UV7L5ND3EH8T 1
next A3UV7L5ND3EH8T 1
week A3UV7L5ND3EH8T 1
always A3UV7L5ND3EH8T 1
quoting A3UV7L5ND3EH8T 1
lines A3UV7L5ND3EH8T 1
movie A3UV7L5ND3EH8T 1
actually A3UV7L5ND3EH8T 1
funny A3UV7L5ND3EH8T 1
movie A3UV7L5ND3EH8T 1
mewhen A3UV7L5ND3EH8T 1
amazon A3UV7L5ND3EH8T 1
talking A3UV7L5ND3EH8T 1
napoleon A3UV7L5ND3EH8T 1
doll A3UV7L5ND3EH8T 1
said A3UV7L5ND3EH8T 1
phrases A3UV7L5ND3EH8T 1
moviewell A3UV7L5ND3EH8T 1
ityou A3UV7L5ND3EH8T 1
push A3UV7L5ND3EH8T 1
button A3UV7L5ND3EH8T 1
base A3UV7L5ND3EH8T 1
hear A3UV7L5ND3EH8T 1
phr

In [ ]:
currentCount = 0
currentKey = None
lastKey = None

for line in spam_mapperout:
    #print(line[1])
    #print(type(line[0]))
    if line != '':
        currentKey=",".join([line[0],line[1]])
        print(currentKey)   
        count = int(line[2])

        if lastKey == currentKey:
            currentCount += count
        else:
            if lastKey:
                print('(%s,%d)' %(lastKey, currentCount))
            currentCount = count
            lastKey = currentKey

if lastKey == currentKey:
    print((lastKey, currentCount))